# 3-7. 言語・知識 - 形態素解析、単語分割、係り受け解析

テキストを「トークン」と呼ばれる表現要素の最⼩単位の集合に分割することを分かち書き（単語分割）と呼び，テキスト（単位として⽂）をトークンに分割し，各トークンに品詞や語形・活⽤形などの情報を付与する処理を形態素解析と呼ぶ．また，それら単語の関係を係り受け構造（依存構造）と呼び，この構造を解析することを係り受け解析という．

実用上ではこれらの処理をどのようにして行っていくのか，ゲームパッケージのタイトルを利用して具体的にみてみよう．

## データの取得・整形
メディア芸術データベース・ラボ上で提供されている[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)を利用して，ゲームパッケージのデータを取得していく．

以下のコードを[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)上に入力して実行する，または入力を省略した[こちらのURL](https://mediag.bunka.go.jp/madb_lab/lod/sparql/#query=PREFIX%20ma%3A%20%3Chttps%3A%2F%2Fmediaarts-db.bunka.go.jp%2Fdata%2Fproperty%23%3E%0APREFIX%20rdfs%3A%20%20%20%3Chttp%3A%2F%2Fwww.w3.org%2F2000%2F01%2Frdf-schema%23%3E%0APREFIX%20schema%3A%20%3Chttps%3A%2F%2Fschema.org%2F%3E%20SELECT%20%3F%E3%83%A9%E3%83%99%E3%83%AB%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5%0AWHERE%20%7B%0A%20%20%3F%E3%82%A2%E3%82%A4%E3%83%86%E3%83%A0%0A%20%20%20%20%20%20%20%20schema%3Agenre%20%22%E3%82%B2%E3%83%BC%E3%83%A0%E3%83%91%E3%83%83%E3%82%B1%E3%83%BC%E3%82%B8%22%3B%0A%20%20%20%20%20%20%20%20schema%3AcontentRating%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%3B%0A%20%20%20%20%20%20%20%20schema%3AgamePlatform%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%3B%0A%20%20%20%20%20%20%20%20schema%3Apublisher%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%3B%0A%20%20%20%20%20%20%20%20rdfs%3Alabel%20%3F%E3%83%A9%E3%83%99%E3%83%AB%3B%0A%20%20%20%20%20%20%20%20ma%3AdatePublished%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5.%0A%7D&endpoint=https%3A%2F%2Fmediag.bunka.go.jp%2Fsparql&requestMethod=POST&tabTitle=Query&headers=%7B%7D&contentTypeConstruct=application%2Fn-triples%2C*%2F*%3Bq%3D0.9&contentTypeSelect=application%2Fsparql-results%2Bjson%2C*%2F*%3Bq%3D0.9&outputFormat=table)から実行してデータを取得できる．

取得したCSVファイルを「ゲームパッケージ.csv」として保存し，このノートブック上にアップロードしよう．

※「3-4. ディープニューラルネットワーク（DNN）」，「3-4. 学習用データと学習済みモデル」，「3-6. 決定木」，「3-6. サポートベクターマシン」，「3-7. かな漢字変換」，「3-7. 表現学習」と同じデータセットを作成するため，もし同じものを持っている場合は以下の取得作業は不要なので，そちらをアップロードしよう．

```
PREFIX ma: <https://mediaarts-db.bunka.go.jp/data/property#>
PREFIX rdfs:   <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema: <https://schema.org/> SELECT ?ラベル ?発行者 ?プラットフォーム ?レーティング ?公開年月日
WHERE {
  ?アイテム
        schema:genre "ゲームパッケージ";
        schema:contentRating ?レーティング;
        schema:gamePlatform ?プラットフォーム;
        schema:publisher ?発行者;
        rdfs:label ?ラベル;
        ma:datePublished ?公開年月日.
}
```

取得したデータセットを，Python上で扱いやすい形にしていく．
pandasというライブラリを用いて，csv形式のファイルの中身をDataFrameという型に変換し，扱っていく．

In [1]:
# 必要なモジュールのインポート
!pip install mecab-python3
!pip install unidic-lite
!pip install pyknp
import MeCab
from pyknp import KNP
from pyknp import Juman
import pandas as pd
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer
import re

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 581.7/581.7 kB 9.4 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.4/47.4 MB 17.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for unidic-lite: filename=unidic_lite-1.0.8-py3-none-any.whl size=47658817 sha256=78d4500ae627f9f5f21a2de8e777e3ea7c62362df89a614b187f3d3f3fd24e71
  Stored in directory: /root/.cache/pip/wheels/89/e8/68/f9ac36b8cc6c8b3c96888cd57434abed96595d444f42243853
Successfully built unidic-lite
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.5/42.5 kB 1.5 MB/s eta 0:00:00


In [2]:
games = pd.read_csv("/content/ゲームパッケージ.csv")
games = games.drop_duplicates(subset='ラベル')
games = games.reset_index(drop=True)
games

ラベル  \
0                           Dance Dance Revolution GB2   
1                                     プロ野球 ファミスタ リターンズ   
2                                      プロ野球 ファミスタ 2011   
3                                              フロッガー3D   
4                                           ブレイブリーセカンド   
...                                                ...   
19452                 バイオショック インフィニット PlayStation Now版   
19453  バイオハザード リベレーションズ アンベールド エディション PlayStation Now版   
19454                           巫剣神威控 PlayStation Now版   
19455                 ネバーエンディング ナイトメア PlayStation Now版   
19456                   雷電IV OverKill PlayStation Now版   

                           発行者       プラットフォーム            レーティング       公開年月日  
0                      コナミ株式会社         ゲームボーイ  CERO D (17才以上対象)  2000-11-16  
1        株式会社バンダイナムコエンターテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2015-10-08  
2              株式会社バンダイナムコゲームス      ニンテンドー3DS    CERO A (全年齢対象)  2011-03-31  
3         株式会社コナミデジタルエンタテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2011-09-22  
4              株式会社スクウェア・エニックス      ニンテンドー3DS  CERO C (15才以上対象)  2015-04-23  
...                        ...            ...               ...         ...  
19452  テイクツー・インタラクティブ・ジャパン合同会社  プレイステーション Now  CERO D (17才以上対象)  2017-09-19  
19453                 株式会社カプコン  プレイステーション Now  CERO D (17才以上対象)  2016-09-20  
19454           アクティブゲーミングメディア  プレイステーション Now  CERO C (15才以上対象)  2017-07-20  
19455           アクティブゲーミングメディア  プレイステーション Now  CERO D (17才以上対象)  2017-07-20  
19456                       モス  プレイステーション Now    CERO A (全年齢対象)  2017-02-21  

[19457 rows x 5 columns]

## 単語分割（分かち書き）
英語の文章は「I have a pen.」のように単語はスペースで区切られているのに対し，日本語の文章は「私はペンを持っている．」のように単語が全て連結した文章になっているため，スペースで区切るような手法で単語分割をすることが難しい．

そこで，こういった日本語データに対する分かち書きをするためのモジュールがいくつか用意されているため，それを利用して分かち書きを行ってみよう．

今回はMeCabというモジュールを利用する．

In [3]:
# 分かち書きを行うインスタンスwakatiの作成
wakati = MeCab.Tagger('-Owakati')

# 試しに，ゲームタイトルを一つ分かち書きにしてみる
# strip()で最後の改行文字列を削除している
wakati.parse(games['ラベル'][0]).strip()

'Dance Dance Revolution GB 2'

このように日本語の文章をスペース区切りの文字列に変換することができる．
これを全てのゲームタイトルに適用するとこのようになる．

In [4]:
# 分かち書きしたタイトルを格納するリスト
wakati_titles = []

for title in games['ラベル']:
  wakati_titles.append(wakati.parse(title).strip())

# 最初から5個目まで見てみる
wakati_titles[:5]

['Dance Dance Revolution GB 2',
 'プロ 野球 ファミスタ リターン ズ',
 'プロ 野球 ファミスタ 2011',
 'フロッガー 3 D',
 'ブレイブリーセカンド']

## 形態素解析

単語分割（分かち書き）と同じように，形態素解析もMeCabを利用して行うことができる．

In [5]:
# 試しに，ゲームタイトルを一つ形態素解析してみる
node = wakati.parseToNode(games['ラベル'][0])

while node:
  word = node.surface
  word_class = node.feature
  print("トークン：　", word)
  print("品詞：　", word_class)
  print()
  node = node.next

トークン：　 
品詞：　 BOS/EOS,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*

トークン：　 Dance
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 Dance
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 Revolution
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 GB
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 2
品詞：　 名詞,数詞,*,*,*,*

トークン：　 
品詞：　 BOS/EOS,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*,*



ここで，最初と最後に現れる「BOS/EOS」というのは自然言語などを扱う時にはよく出てくるもので，「Begin Of Sentence」，「End Of Sentence」のことであり，文章のはじめと終わりを表す特別なトークンである．
これらは文章を生成したりする時には学習が必要だが，不要な時には以下のようにループ文を工夫することで取り除くこともできる．

In [6]:
# BOS/EOSを無視するバージョン
node = wakati.parseToNode(games['ラベル'][0])
node = node.next
while node.next:
  word = node.surface
  word_class = node.feature
  print("トークン：　", word)
  print("品詞：　", word_class)
  print()
  node = node.next

トークン：　 Dance
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 Dance
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 Revolution
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 GB
品詞：　 名詞,普通名詞,一般,*,*,*

トークン：　 2
品詞：　 名詞,数詞,*,*,*,*



全てのゲームタイトルに適用する場合は次のようになる．

In [7]:
# 形態素解析したタイトルを格納するリスト
hinshi = []

for title in games['ラベル']:
  node = wakati.parseToNode(title)
  node = node.next
  # 形態素解析後のタイトルを[[トークン，品詞], [トークン，品詞], ...]のように保存するリスト
  title_hinshi = []
  while node.next:
    word = node.surface
    word_class = node.feature
    title_hinshi.append([word, word_class])
    node = node.next
  hinshi.append(title_hinshi)

# 最初から5個目まで見てみる
for title in hinshi[:5]:
  for token in title:
    print(token[0])
    print(token[1])
    print()
  print("==========================================")

Dance
名詞,普通名詞,一般,*,*,*

Dance
名詞,普通名詞,一般,*,*,*

Revolution
名詞,普通名詞,一般,*,*,*

GB
名詞,普通名詞,一般,*,*,*

2
名詞,数詞,*,*,*,*

プロ
名詞,普通名詞,一般,*,*,*,プロ,プロ-pro,プロ,プロ,プロ,プロ,外,*,*,*,*,プロ,プロ,プロ,プロ,*,*,1,C1,*

野球
名詞,普通名詞,一般,*,*,*,ヤキュウ,野球,野球,ヤキュー,野球,ヤキュー,漢,*,*,*,*,ヤキュウ,ヤキュウ,ヤキュウ,ヤキュウ,*,*,0,C2,*

ファミスタ
名詞,普通名詞,一般,*,*,*

リターン
名詞,普通名詞,サ変可能,*,*,*,リターン,リターン-return,リターン,リターン,リターン,リターン,外,*,*,*,*,リターン,リターン,リターン,リターン,*,*,2,C1,*

ズ
記号,一般,*,*,*,*,ズ,ズ,ズ,ズ,ズ,ズ,記号,*,*,*,*,ズ,ズ,ズ,ズ,*,*,1,*,*

プロ
名詞,普通名詞,一般,*,*,*,プロ,プロ-pro,プロ,プロ,プロ,プロ,外,*,*,*,*,プロ,プロ,プロ,プロ,*,*,1,C1,*

野球
名詞,普通名詞,一般,*,*,*,ヤキュウ,野球,野球,ヤキュー,野球,ヤキュー,漢,*,*,*,*,ヤキュウ,ヤキュウ,ヤキュウ,ヤキュウ,*,*,0,C2,*

ファミスタ
名詞,普通名詞,一般,*,*,*

2011
名詞,数詞,*,*,*,*

フロッガー
名詞,固有名詞,一般,*,*,*,フロッガー,フロッガー,フロッガー,フロッガー,フロッガー,フロッガー,固,*,*,*,*,フロッガー,フロッガー,フロッガー,フロッガー,*,*,2,*,*

3
名詞,数詞,*,*,*,*

D
名詞,普通名詞,一般,*,*,*

ブレイブリーセカンド
名詞,普通名詞,一般,*,*,*

